In [100]:
import numpy as np
import pandas as pd
import pystan
from scipy.stats import norm, multivariate_normal, invwishart, invgamma
from statsmodels.tsa.stattools import acf
import datetime
import sys
import os

from codebase.plot import * 
from codebase.file_utils import save_obj, load_obj
from codebase.post_process import * 

%matplotlib inline

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [101]:
df = pd.read_csv("../dat/muthen_men.csv")
df.head()

y1  y2  y3  y4  y5  y6  y7  y8  y9  y10  y11  y12  y13  y14  y15
0   4   4   6   7   7   6   7   7   7    7    4    7    7    3    7
1   3   4   6   6   5   5   3   5   5    6    7    5    5    6    6
2   2   3   4   5   5   3   3   3   2    6    3    4    5    6    4
3   7   6   6   5   5   5   5   5   3    3    3    3    5    6    6
4   6   6   5   5   6   6   4   4   4    7    5    6    3    4    4

In [102]:
data = dict()
data['N'] = df.shape[0]
data['K'] = 5
data['J'] = df.shape[1]
data['y'] = df.values

In [4]:
stan_data = dict(N = data['N'], K = data['K'], J = data['J'], yy = data['y'])

In [10]:
with open('./codebase/stan_code/cont/CFA/marg_m.stan', 'r') as file:
    model_code = file.read()
print(model_code)

data {
  int<lower=1> N;
  int<lower=1> K;
  int<lower=1> J;
  matrix[N,J] yy;
}

transformed data{
  real<lower=0> c = 1;
  vector[J] zeros = rep_vector(0, J);
  cov_matrix[J] I_c = diag_matrix(rep_vector(c, J));
}

parameters {
  vector<lower=0>[J] sigma;
  vector<lower=0>[K] sigma_z;
  vector[J] alpha;
  matrix[2,K] beta_free; // 2 free eleements per factor
  matrix[J-3,K] beta_zeros; // 3 zero elements per factor
  cholesky_factor_corr[K] V_corr_chol;
  matrix[N,J] uu;
  cov_matrix[J] Sigma_u;
}

transformed parameters{
  cov_matrix[J] Sigma_epsilon;
  matrix[J,K] beta;
  cov_matrix [K] V ;
  cov_matrix[J] Omega;
  
  Sigma_epsilon = diag_matrix(square(sigma));
  V = multiply_lower_tri_self_transpose(diag_pre_multiply(sigma_z, V_corr_chol));

  for(j in 1:J) {
    for (k in 1:K) beta[j,k] = 0;
  }
  
  // set ones
  for (k in 1:K) beta[1+3*(k-1), k] = 1;

  // set the free elements
  for (k in 1:K) beta[2+3*(k-1) : 3+3*(k-1), k] = beta_free[1:2,k];

  // set the zero elements
  bet

In [11]:
sm = pystan.StanModel(model_code=model_code, verbose=False)

INFO:pystan:COMPILING THE C++ CODE FOR MODEL anon_model_9498c524cd6a14b9b17833cb43c87e84 NOW.


In [15]:
nowstr = datetime.datetime.now().strftime('%Y%m%d_%H%M%S_') # ISO 8601 format
task_id = 'CFA_NN_marg_muthen_men'
log_dir =  "./log/"+nowstr+"%s/" % task_id

In [16]:
if not os.path.exists(log_dir):
    os.makedirs(log_dir)

In [12]:
fit_opt = sm.optimizing(data=stan_data)


In [5]:
num_chains = 1
num_samples = 1000
num_warmup = 1000
num_iter = num_samples + num_warmup

In [18]:
fit_run = sm.sampling(data=stan_data, iter=num_iter, warmup=num_warmup, chains=num_chains)

To run all diagnostics call pystan.check_hmc_diagnostics(fit)


In [19]:
save_obj(sm, 'sm', log_dir)
save_obj(fit_run, 'fit', log_dir)
fit=fit_run

/Users/itemgmt/myPhD/factor-analysis/src/codebase/file_utils.py:7: UserWarning: Pickling fit objects is an experimental feature!
The relevant StanModel instance must be pickled along with this fit object.
When unpickling the StanModel must be unpickled first.
  pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)


In [20]:
print(log_dir)

./log/20190421_092254_CFA_NN_marg_muthen_men/


In [6]:
log_dir = "./log/20190421_092254_CFA_NN_marg_muthen_men/"
sm = load_obj('sm', log_dir)
fit = load_obj('fit', log_dir)



In [107]:
param_names = ['Omega_beta', 'beta', 'V_corr', 'V' , 'uu', 'alpha', 'sigma', 'sigma_z']

stan_samples= fit.extract(permuted=False, pars=param_names)  # return a dictionary of arrays

if num_chains ==1:
    ps = dict()
    for name in param_names:
        ps[name] = np.squeeze(stan_samples[name])
else: 
    ps = stan_samples

In [8]:
mb = np.zeros((data['J'], data['K']))
mb[:3,0] = np.array([0.842, 0.394, 0.479 ])
mb[3:6,1] = np.array([0.683, 0.078, 0.579 ])
mb[6:9,2] = np.array([0.748, 0.754, 0.575])
mb[9:12,3] = np.array([0.801, 0.708, 0.613])
mb[12:,4] = np.array([0.732, 0.672, 0.651])


In [9]:
muthen_results = dict()
muthen_results['beta'] = mb


In [10]:
our_results=dict()
our_results['beta'] = np.average(ps['beta'], axis=0)

In [11]:
muthen_results['beta'][:,0]

array([0.842, 0.394, 0.479, 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   ])

In [28]:
for i in range(5):
    print("%d,%d= %.1f"%(3*i,i,ps['beta'][0,3*i,i]))

0,0= 1.0
3,1= 1.0
6,2= 1.0
9,3= 1.0
12,4= 1.0


In [30]:
%%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
plots = []
for i in range(data['J']):
    for j in range(data['K']):
            plots.append(plot_trace(ps['Omega_beta'][:,i,j],
                     true_value=None,
                     title = 'Posterior distribution for Omega_beta(%s,%s)'%(i,j)))
layout = hv.Layout(plots)
layout.cols(1)

:Layout
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_0_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_0_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_0_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_0_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_0_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_1_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_1_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_1_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_1_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_1_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_2_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_2_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_2_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_2_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_2_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_3_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_3_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_3_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_3_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_3_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_4_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_4_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_4_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_4_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_4_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_5_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_5_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_5_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_5_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_5_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_6_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_6_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_6_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_6_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_Omega_beta_left_parenthesis_6_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_

In [31]:
%%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
plots = []
for i in range(data['J']):
    for j in range(data['K']):
            plots.append(plot_trace(acf(ps['Omega_beta'][:,i,j]),
                     title = 'Autocorrelation of Omega(%s,%s)'%(i,j)))
layout = hv.Layout(plots)
layout.cols(1)

:Layout
   .Curve.Autocorrelation_of_Omega_left_parenthesis_0_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_0_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_0_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_0_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_0_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_1_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_1_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_1_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_1_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_1_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_2_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_2_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_2_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_2_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_2_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_3_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_3_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_3_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_3_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_3_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_4_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_4_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_4_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_4_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_4_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_5_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_5_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_5_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_5_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_5_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_6_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_6_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_6_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_6_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_6_comma_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_7_comma_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_7_comma_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_7_comma_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_7_comma_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Autocorrelation_of_Omega_left_parenthesis_7_comma_4_right_parenthesis  :Curve   [x

In [32]:
%%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
plots = []
for i in range(data['J']):
    for j in range(data['K']):
            plots.append(plot_trace(ps['beta'][:,i,j],
                     true_value=muthen_results['beta'][i,j],
                     title = 'Posterior distribution for beta(%s,%s)'%(i,j)))
layout = hv.Layout(plots)
layout.cols(1)

:Layout
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_0_comma_0_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_0_comma_1_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_0_comma_2_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_0_comma_3_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_0_comma_4_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_1_comma_0_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_1_comma_1_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_1_comma_2_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_1_comma_3_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_1_comma_4_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_2_comma_0_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_2_comma_1_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_2_comma_2_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_2_comma_3_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_2_comma_4_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_3_comma_0_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_3_comma_1_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_3_comma_2_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_3_comma_3_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_3_comma_4_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_4_comma_0_right_parenthesis  :Overlay
      .Curve.Samples    :Curve   [x]   (y)
      .Curve.True_Value :Curve   [x]   (y)
   .Overlay.Posterior_distribution_for_beta_left_parenthesis_4_comma_1_right_parenthesis  :Overlay
      .C

In [16]:
# %%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
# plots = []
# for i in range(data['J']):
#             plots.append(plot_trace(ps['alpha'][:,i],
#                      true_value=data['alpha'][i],
#                      title = 'Posterior distribution for mu(%s)'%(i)))
# layout = hv.Layout(plots)
# layout.cols(1)

In [17]:
# %%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
# plots = []
# for i in range(data['J']):
#             plots.append(plot_trace(acf(ps['alpha'][:,i]),
#                      title = 'Autocorrelation of alpha(%s)'%(i)))
# layout = hv.Layout(plots)
# layout.cols(1)

In [125]:
%%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
plots = []
for i in range(data['J']):
            plots.append(plot_trace(ps['sigma'][:,i],
                     true_value=None,
                     title = 'Posterior distribution for sigma(%s)'%(i)))
layout = hv.Layout(plots)
layout.cols(1)

:Layout
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_0_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_1_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_2_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_3_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_4_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_5_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_6_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_7_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_8_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_9_right_parenthesis  :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_10_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_11_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_12_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_13_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_sigma_left_parenthesis_14_right_parenthesis :Curve   [x]   (y)

In [103]:
def get_residuals(ps_u, by_axis, absval = True, sort=False):
    """
    params
    ps_u posterior samples of u
    by_axis 0=residuals per iterm, 1=residuals per subject
    """
    mean_u = np.mean(ps_u, axis=0) #mean posterior residual matrix
    std_u = np.sqrt(np.mean(ps_u**2, axis=0)- mean_u**2) #std of posterior residual matrix
    if absval:
        res = pd.DataFrame(np.sum(np.abs(mean_u/std_u), axis=by_axis)).reset_index()
    else:
        res = pd.DataFrame(np.sum(mean_u/std_u, axis=by_axis)).reset_index()
    res.columns = ['index', 'residual']
    
    if sort:
        res.sort_values('residual', ascending=False, inplace=True)
    return res

get_residuals(ps['uu'], 1, True, True)


index   residual
160    160  54.221904
414    414  52.032385
241    241  50.191464
225    225  30.990491
168    168  30.781598
90      90  30.506787
284    284  25.966135
445    445  25.859169
359    359  25.633278
500    500  24.683649
55      55  23.525431
92      92  23.357858
157    157  22.099574
200    200  21.650569
433    433  21.309408
571    571  19.919830
434    434  19.797791
88      88  19.565370
161    161  19.533958
549    549  19.304778
485    485  19.247204
184    184  19.242976
535    535  18.334711
503    503  17.524542
256    256  17.174262
57      57  17.097062
570    570  17.089957
120    120  16.793715
362    362  16.444457
476    476  16.302093
..     ...        ...
469    469   2.781869
41      41   2.768222
18      18   2.755360
424    424   2.745777
255    255   2.734853
471    471   2.731524
402    402   2.723660
341    341   2.701745
539    539   2.676750
128    128   2.644820
370    370   2.624893
516    516   2.616872
133    133   2.582808
118    118   2.561955
148    148   2.534225
44      44   2.445367
43      43   2.443572
569    569   2.244863
175    175   2.182198
489    489   2.160984
149    149   2.149759
192    192   2.127229
472    472   2.099944
64      64   2.091938
216    216   2.035373
7        7   1.830060
526    526   1.705864
536    536   1.604075
408    408   1.601575
42      42   1.166415

[589 rows x 2 columns]

In [104]:
%%opts Bars {+axiswise} [width=1000, height=300, tools=['hover']] 
res = get_residuals(ps['uu'], 1, True, True)

hv.Bars(res, hv.Dimension('index'), 'residual',\
        label='Residuals').options(color='blue', xrotation=90)


:Bars   [index]   (residual)

In [120]:
%%opts BoxWhisker {+axiswise} [width=1000, height=300, tools=['hover']] 

plots = []

for j in range(15):
    plots.append(hv.BoxWhisker((j, ps['uu'][:,160,j]), 'Index', 'Value',\
                               label='Subject 160').options(box_color='blue', box_alpha=0.4, xrotation=90))
    plots.append(hv.BoxWhisker((j, ps['uu'][:,414,j]), 'Index', 'Value',\
                           label='Subject 141').options(box_color='red', box_alpha=0.4, xrotation=90))
    plots.append(hv.BoxWhisker((j, ps['uu'][:,241,j]), 'Index', 'Value',\
                       label='Subject 241').options(box_color='green', box_alpha=0.4, xrotation=90))

layout = hv.Overlay(plots).le
layout.cols(1)

:Overlay
   .BoxWhisker.Subject_160.I    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.I    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.I    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.II   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.II   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.II   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.III  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.III  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.III  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.IV   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.IV   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.IV   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.V    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.V    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.V    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.VI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.VI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.VI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.VII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.VII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.VII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.VIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.VIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.VIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.IX   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.IX   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.IX   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.X    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.X    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.X    :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.XI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.XI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.XI   :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.XII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.XII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.XII  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.XIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.XIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.XIII :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_160.XIV  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_141.XIV  :BoxWhisker   [Index]   (Value)
   .BoxWhisker.Subject_241.XIV  :BoxWhisker   [Index]   (Value)

In [128]:
%%opts Curve {+axiswise} [width=600, height=200, tools=['hover']] 
plots = []
for i in range(data['K']):
    for j in range(data['K']):
        if i<j:
            plots.append(plot_trace(ps['V_corr'][:,i,j],
                     true_value=None,
                     title = 'Posterior distribution for V-correlations(%s,%s)'%(i,j)))
layout = hv.Layout(plots)
layout.cols(1)

:Layout
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_0_comma_1_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_0_comma_2_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_0_comma_3_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_0_comma_4_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_1_comma_2_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_1_comma_3_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_1_comma_4_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_2_comma_3_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_2_comma_4_right_parenthesis :Curve   [x]   (y)
   .Curve.Posterior_distribution_for_V_hyphen_minus_correlations_left_parenthesis_3_comma_4_right_parenthesis :Curve   [x]   (y)